In [1]:
import sys
import torch
import os

In [2]:
os.chdir("..")

In [3]:
!ls

README.md	  notebooks	      scripts	    vt-tr.o7146959
checkpoints	  out.txt	      src	    vt-tr.o7209762
data		  prose_translations  training	    vt-tr.o7242335
jupyter.o7250076  requirements.txt    translations
logs		  runs		      venv


In [4]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [5]:
from src.data_utils.batch import rebatch
from src.data_utils.data import get_training_iterators
from src.model.loss_optim import MultiGPULossCompute, SimpleLossCompute
from src.model.model import make_model, NoamOpt, LabelSmoothing, translate_sentence
from src.utils.utils import get_tokenizer

In [6]:
tok = get_tokenizer("tr")

In [7]:
train_iter, valid_iter, test_iter, train_idx, dev_idx, test_idx = get_training_iterators("tur")

/auto/praha1/memduh/versetorch/venv/lib/python3.6/site-packages/torchtext/data/field.py:150: UserWarning: Field class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/auto/praha1/memduh/versetorch/venv/lib/python3.6/site-packages/torchtext/data/example.py:78: UserWarning: Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.', UserWarning)
/auto/praha1/memduh/versetorch/venv/lib/python3.6/site-packages/torchtext/data/iterator.py:48: UserWarning: MyIterator class will be retired soon and moved to torchtext.l

In [11]:
# mini dev set
with open("data/tr/tur.dev.tgt", encoding="utf-8") as infile:
    toystrings = [x.strip() for x in infile.readlines()[:20]]

In [12]:
toyset = [torch.LongTensor([1] + tok.Encode(x) + [2])  for x in toystrings]
toyset = torch.nn.utils.rnn.pad_sequence(sequences=toyset, padding_value=3)

In [13]:
toyset

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 5605,     8,  1330,  ...,     8,   771,  2804],
        [27861,  2475, 10284,  ...,  3987,  5057, 11694],
        ...,
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3]])

Two critics:
- Input related to output or not
- Classifier into poetry, prose, generated, scrambled poetry

One word/token selector:
- Choose tokens from input sequence to use for topic
- 

In [14]:
from torchtext import data
import torchtext as tt
from src.data_utils.batch import MyIterator
from src.model.model import batch_size_val

def each_line(fname):
    c = 0
    lines = []
    with open(fname, "r", encoding="utf-8") as infile:
        for line in infile:
            if line.count(" ") > 200:
                continue
            lines.append(line.strip())
            c += 1
            if c >= 2000000: 
                break
    return lines

def make_iter(fpath, tokenizer, batch_size=256):
    dev = each_line(fpath)
    
    def tok(seq):
        return tokenizer.EncodeAsIds(seq)

    field = data.Field(tokenize=tok, init_token=1, eos_token=2, pad_token=3, use_vocab=False)
    #ds = data.TabularDataset(fpath, "tsv", [("src", field)], skip_header=True)

    examples = [tt.data.Example.fromdict({"src": x}, {"src": ("src", field)}) for x in dev]
    ds = tt.data.Dataset(examples, {"src": field})
    iter = MyIterator(ds, batch_size=batch_size, device="cpu",
                             repeat=False, sort_key=lambda x: len(x.src),
                             batch_size_fn=batch_size_val, train=False, sort=True)

    return iter

prose_iter = make_iter("data/tr/prose/prose_gan.txt", tok)

/auto/praha1/memduh/versetorch/venv/lib/python3.6/site-packages/torchtext/data/example.py:52: UserWarning: Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.', UserWarning)


In [15]:
ntokens = 32000
enc_dec = make_model(ntokens, ntokens, N=6).to(device)
token_selector = make_model(ntokens, 2, N=2).to(device)
critic = make_model(ntokens, 4, N=2).to(device)

/auto/plzen1/home/memduh/versetorch/src/model/model.py:264: UserWarning: nn.init.xavier_uniform is now deprecated in favor of nn.init.xavier_uniform_.
  nn.init.xavier_uniform(p)


EncoderDecoder(
  (encoder): Encoder(
    (layers): ModuleList(
      (0): EncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linears): ModuleList(
            (0): Linear(in_features=512, out_features=512, bias=True)
            (1): Linear(in_features=512, out_features=512, bias=True)
            (2): Linear(in_features=512, out_features=512, bias=True)
            (3): Linear(in_features=512, out_features=512, bias=True)
          )
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (feed_forward): PositionwiseFeedForward(
          (w_1): Linear(in_features=512, out_features=2048, bias=True)
          (w_2): Linear(in_features=2048, out_features=512, bias=True)
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (sublayer): ModuleList(
          (0): SublayerConnection(
            (norm): LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): SublayerConnection(
            (norm): LayerNorm()

In [16]:
from torch.autograd import Variable
import numpy as np
def subsequent_mask(size):
    "Mask out subsequent positions."
    attn_shape = (1, size, size)
    subsequent_mask = np.triu(np.ones(attn_shape), k=1).astype('uint8')
    return torch.from_numpy(subsequent_mask) == 0


def prep_tensors( src, trg, pad=3):
    src_mask = (src != pad).unsqueeze(-2)
    trg_in = trg[:, :-1]
    trg_y = trg[:, 1:]
    trg_mask = make_std_mask(trg_in, pad)
    return src, trg_y, src_mask, trg_mask

def make_std_mask(tgt, pad):
    """Create a mask to hide padding and future words."""
    tgt_mask = (tgt != pad).unsqueeze(-2)
    tgt_mask = tgt_mask & Variable(
        subsequent_mask(tgt.size(-1)).type_as(tgt_mask.data))
    return tgt_mask


In [30]:
dummy = torch.ones(toyset.shape, dtype=torch.long)

In [44]:
toyset.shape

torch.Size([359, 20])

In [45]:
select_prob_embeds = token_selector.forward(toyset.to(device), 
                                     dummy.to(device),
                                     (toyset != 3).unsqueeze(-2).to(device),  
                                     make_std_mask(dummy, 3).to(device))
select_prob = token_selector.generator(select_prob_embeds)

In [56]:
select_indices = torch.max(select_prob, dim=2).indices.type(torch.ByteTensor)

In [70]:
dae_list = []
for ind, row in zip(select_indices, toyset):
    dae_list.append(torch.masked_select(row, ind)[:15])
torch.nn.utils.rnn.pad_sequence(dae_list, batch_first=True, padding_value=3)

/auto/praha1/memduh/versetorch/venv/lib/python3.6/site-packages/ipykernel_launcher.py:3: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead. (Triggered internally at  /pytorch/aten/src/ATen/native/TensorAdvancedIndexing.cpp:733.)
  This is separate from the ipykernel package so we can avoid doing imports until


tensor([[    1,     3,     3,  ...,     3,     3,     3],
        [ 1330,     8,     3,  ...,     3,     3,     3],
        [10171,   850, 20193,  ...,     3,     3,     3],
        ...,
        [    3,     3,  7926,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3]])

tensor([[    1,     3,     3,  ...,     3,     3,     3],
        [ 1330,     8,     3,  ...,     3,     3,     3],
        [10171,   850, 20193,  ...,     3,     3,     3],
        ...,
        [    3,     3,  7926,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3]])

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 5605,     8,  1330,  ...,     8,   771,  2804],
        [27861,  2475, 10284,  ...,  3987,  5057, 11694],
        ...,
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3],
        [    3,     3,     3,  ...,     3,     3,     3]])

In [17]:
for poetry_batch, prose_batch in zip(train_iter, prose_iter):
    tgt, tgt_mask = poetry_batch.trg.to(device), poetry_batch.trg_mask.to(device)
    
    # classify tokens, get the first 15 tokens selected.
    
    # create src and src mask from selected tokens
    
    # src and tgt for style critic
    
    # src and tgt for relevance critic

Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.
Skipped overlong sample while batching.


tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 1330,   368,     8,  ...,     8, 18653,     8],
        [  621,  2826, 23698,  ...,  1266,  6950, 15101],
        ...,
        [14587, 30103,  1660,  ...,  8085,  9206,   475],
        [   45,    18,    18,  ...,    32,    18,    18],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 4712,     8,     8,  ...,     8,     9, 10299],
        [12694, 25609,  3516,  ...,  1490,  4452,    20],
        ...,
        [  195,  5454,   165,  ...,   922,  5509, 14073],
        [   18,    18,    42,  ...,  1465,   375,    13],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,  5532,  1484,  ...,     8,     8,  5869],
        [21613,    74,   960,  ...,  1104,  1488,     5],
        ...,
        [   25,   867,  3040,  ...,    81,  1035,   694],
        [   18,  1395,  3511,  

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  745,     8,   270,  ..., 10346, 12860,  1484],
        [ 1677,  2545,   514,  ...,   777, 24092,   407],
        ...,
        [   10,   195,  4461,  ...,    87,  6405,   469],
        [   42,    18,  5881,  ...,    18,   396,    18],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  779,     8,  5566,  ...,     8, 10848,     8],
        [ 7862,  2647,  1200,  ...,  1857,    62,  2184],
        ...,
        [ 4761,  2482,  7849,  ..., 11960,   114,   839],
        [   18,    18,   833,  ...,    18,    18,  1114],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  771, 14619,  1038,  ...,  8015, 20625,     8],
        [    5,   204,  1621,  ...,   463,    25, 31939],
        ...,
        [ 9242,    34, 15300,  ...,    24,     4,    62],
        [   42,  4741,    18,  

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 4288,   779,   779,  ...,  1027,     8,     8],
        [ 3287,  2050,    85,  ...,     5,  5386,  2694],
        ...,
        [   87, 14450,  1852,  ...,    68, 29485,  1670],
        [   18,    18,    18,  ...,    42,  2011,    82],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  270,     8,     8,  ...,     8,     8,   779],
        [  332,  8310,  2233,  ..., 21879,  1851,   799],
        ...,
        [ 1940,    40,    14,  ...,    24, 24877,  1330],
        [   18,    18, 17572,  ...,   994,    18,  8875],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  779,     8,     8,  ..., 13824,     8,   779],
        [  551, 19035, 18085,  ...,  1689,  4334,   147],
        ...,
        [ 7790, 12033,  5327,  ...,   168,    82,   112],
        [   18,    18,    18,  

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,     8,     8,  ...,     8,     8,  3716],
        [ 8900, 31253,   518,  ...,  9940,     0,  1257],
        ...,
        [10869,    82,  1670,  ...,   248, 11762,   396],
        [    0,  2213,    61,  ...,    18,    42,    18],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8, 10187,     8,  ...,   932, 19081,   270],
        [31167,  9064,  4631,  ...,    90,  1649,   119],
        ...,
        [ 3444,  3351, 12210,  ...,   152, 30898, 24437],
        [  375,  1019, 23279,  ...,    18,   875,    18],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,     8,  9361,  ...,  1484,     8,   779],
        [ 2475,  9293,    22,  ...,    60, 17161,    49],
        ...,
        [  112,   188,  3010,  ...,  1500,   206,   188],
        [ 4893,  1126,   175,  

...

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,  4944,  9245,  ...,     8, 17545,     8],
        [18327,   159,   848,  ..., 27342,  1766, 13514],
        ...,
        [   96,     0,  7218,  ...,  8562, 30110, 10345],
        [   18,  1727,  5014,  ...,    42,    18,  3669],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,     8,  7488,  ...,  5532,   270,     8],
        [22823,  3938,     9,  ...,   642,  1626, 21586],
        ...,
        [  922,     4,    71,  ...,  1423,    20,  2303],
        [   42,   183, 17190,  ...,  1657,  5393,   169],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,   351,  1330,  ...,   745,     8,  6246],
        [ 1147,   244,  8703,  ...,  7360, 20041,  3021],
        ...,
        [   24,     4,    23,  ...,  2651,    62,    53],
        [ 3764, 17850,    18,  

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [10258,   932,     8,  ...,  4288,     8,   771],
        [  126,    71,  9656,  ..., 16857, 31130,   449],
        ...,
        [   81,  5325,   910,  ...,   411,  6403,   537],
        [  118,    18, 10982,  ...,    18,    18,    42],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,     8,     8,  ...,     8, 13025,     8],
        [24718,     0,  1609,  ..., 21569,    22,  3993],
        ...,
        [   18,   350,   154,  ...,    87,    13, 18834],
        [    2,    18,  9870,  ...,   375,  2801,    42],
        [    3,     2,     2,  ...,     2,     2,     2]])
tensor([[   1,    1,    1,  ...,    1,    1,    1],
        [1330,    8,    8,  ...,    8, 4179,    8],
        [3067, 3630, 1466,  ..., 3438,   36, 5554],
        ...,
        [  18,   49,  200,  ..., 2911,   21, 6570],
        [  35,   18,   18,  ...,   18,   18,   18],
   

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [  192,    36, 18756,  ...,     8,   270,     8],
        [ 2464,  4776,   431,  ..., 17273,  2078, 27877],
        ...,
        [  243,    13,    82,  ...,    25,    16,  1336],
        [  529, 24726,  1953,  ...,     5,    42,  4056],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [   60,     8,  4491,  ...,     8,     8,   771],
        [10716,  5085,  8136,  ...,  6898,  1197,   252],
        ...,
        [ 1169,     8,  3341,  ...,  3404,  3912,  7975],
        [   18,    18,   375,  ..., 12032,    18,    18],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,  9356,     8,  ...,     8,     8,  1330],
        [16416, 28531,  3295,  ..., 11861,  5921,   400],
        ...,
        [ 5374,   138,   118,  ...,   150, 15411,   559],
        [  994,    42,   833,  

tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8, 12898, 10565,  ...,     8,   745,   525],
        [ 5512,   156,  6273,  ...,  8223,    75,    39],
        ...,
        [ 4063,   145,    40,  ...,  4103, 10764,  1641],
        [22171,    18,  1076,  ...,    42,    40,   118],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [    8,  9245,     8,  ..., 15863,     8,     8],
        [31019,   126,  6639,  ...,   262,  1002, 14042],
        ...,
        [  123,  1547, 11291,  ...,   174,    34,  4139],
        [   18,    42,    18,  ...,    42,    18,   427],
        [    2,     2,     2,  ...,     2,     2,     2]])
tensor([[    1,     1,     1,  ...,     1,     1,     1],
        [ 6457,     8,     8,  ...,     8,     8,  9622],
        [ 1267,  5002, 15504,  ...,   870,  4829,  2558],
        ...,
        [  704,    63,    32,  ..., 15207,    38,    87],
        [  184,  7906,   529,  

KeyboardInterrupt: 